# Steam's videogames platform 👾
960 min
Steam

## Company's description 📇

Steam is a video game digital distribution service and storefront from Valve. It was launched as a software client in September 2003 to provide game updates automatically for Valve's games, and expanded to distributing third-party titles in late 2005. Steam offers various features, like digital rights management (DRM), game server matchmaking with Valve Anti-Cheat measures, social networking, and game streaming services. Steam client's functions include game update automation, cloud storage for game progress, and community features such as direct messaging, in-game overlay functions and a virtual collectable marketplace.

## Project 🚧

You're working for Ubisoft, a French video game publisher. They'd like to release a new revolutionary videogame! They asked you conduct a global analysis of the games available on Steam's marketplace in order to better understand the videogames ecosystem and today's trends.

## Goals 🎯

The ultimate goal of this project is to understand what factors affect the popularity or sales of a video game. But your boss asked you to take advantage of this opportunity to analyze the video game market globally.

To carry out this project, you will have to adopt different levels of analysis. 



## Scope of this project 🖼️

You'll have to use Databricks and PySpark to conduct this EDA. Particularly, you'll have to use Databrick's visualisation tool to create the visualizations.

The dataset is available in our S3 bucket at the following url: [s3://full-stack-bigdata-datasets/Big_Data/Project_Steam/steam_game_output.json](s3://full-stack-bigdata-datasets/Big_Data/Project_Steam/steam_game_output.json).

## Helpers 🦮

To help you achieve this project, here are a few tips that should help you:

To adopt different levels of analysis, it might be useful to create different dataframes.

As the dataset is semi-structured with a nested schema, Pyspark's methods such as getField() and explode() may help you.

There are some text and date fields in this dataset: Pyspark offers utilitary functions to manipulate these types of data efficiently 💡

You can use agregate functions and groupBy to conduct segmented analysis.

## Deliverable 📬

To complete this project, you should deliver:

One or several notebooks including data manipulation with PySpark and data visualization with Databrick's dashboarding tool.

To make sure the jury can view all the visualizations, please use the "publish" button on Databricks notebooks to create a public url where a copy of your notebook will be available.

While using the "publish" button, Databricks may tell you that your notebook's size exceeds the maximal size allowed. If this happens, just split your notebook in several notebooks.

Please copy-paste the link(s) to your published notebooks into your Github repo such that the jury can access it easily. 😌



In [0]:
spark

sc = spark.sparkContext

from pyspark.sql.types import *

from pyspark.sql.types import * # Import types to convert columns using spark sql
from pyspark.sql import functions as F # This will load the class where spark sql functions are contained
from pyspark.sql import Row # this will let us manipulate rows with spark sql

In [0]:
# Bucket d'input : s3://full-stack-bigdata-datasets/Big_Data/Project_Steam/steam_game_output.json
steam_path = "s3://full-stack-bigdata-datasets/Big_Data/Project_Steam/steam_game_output.json"

df = spark.read.json(steam_path)

df.show(5)
df.select('data.release_date').show(5)

+--------------------+-------+
|                data|     id|
+--------------------+-------+
|{10, [Multi-playe...|     10|
|{1000000, [Single...|1000000|
|{1000010, [Single...|1000010|
|{1000030, [Multi-...|1000030|
|{1000040, [Single...|1000040|
+--------------------+-------+
only showing top 5 rows

+------------+
|release_date|
+------------+
|   2000/11/1|
|  2021/05/14|
|  2020/10/16|
|  2020/10/14|
|  2019/03/30|
+------------+
only showing top 5 rows



In [0]:
df.printSchema()

root
 |-- data: struct (nullable = true)
 |    |-- appid: long (nullable = true)
 |    |-- categories: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |    |-- ccu: long (nullable = true)
 |    |-- developer: string (nullable = true)
 |    |-- discount: string (nullable = true)
 |    |-- genre: string (nullable = true)
 |    |-- header_image: string (nullable = true)
 |    |-- initialprice: string (nullable = true)
 |    |-- languages: string (nullable = true)
 |    |-- name: string (nullable = true)
 |    |-- negative: long (nullable = true)
 |    |-- owners: string (nullable = true)
 |    |-- platforms: struct (nullable = true)
 |    |    |-- linux: boolean (nullable = true)
 |    |    |-- mac: boolean (nullable = true)
 |    |    |-- windows: boolean (nullable = true)
 |    |-- positive: long (nullable = true)
 |    |-- price: string (nullable = true)
 |    |-- publisher: string (nullable = true)
 |    |-- release_date: string (nullable = true)
 |    |-

In [0]:
df.schema.jsonValue()

Out[4]: {'type': 'struct',
 'fields': [{'name': 'data',
   'type': {'type': 'struct',
    'fields': [{'name': 'appid',
      'type': 'long',
      'nullable': True,
      'metadata': {}},
     {'name': 'categories',
      'type': {'type': 'array', 'elementType': 'string', 'containsNull': True},
      'nullable': True,
      'metadata': {}},
     {'name': 'ccu', 'type': 'long', 'nullable': True, 'metadata': {}},
     {'name': 'developer', 'type': 'string', 'nullable': True, 'metadata': {}},
     {'name': 'discount', 'type': 'string', 'nullable': True, 'metadata': {}},
     {'name': 'genre', 'type': 'string', 'nullable': True, 'metadata': {}},
     {'name': 'header_image',
      'type': 'string',
      'nullable': True,
      'metadata': {}},
     {'name': 'initialprice',
      'type': 'string',
      'nullable': True,
      'metadata': {}},
     {'name': 'languages', 'type': 'string', 'nullable': True, 'metadata': {}},
     {'name': 'name', 'type': 'string', 'nullable': True, 'metadata'

In [0]:
from pyspark.sql.types import StructType, StructField
from typing import List, Dict, Generator, Union, Callable

# This is actually written like a scala function, we'll walk you through it
def walkSchema(schema: Union[StructType, StructField]) -> Generator[str, None, None]:
    """Explores a PySpark schema:
    
    schema: StructType | StructField
    
    Yield
    -----
    A generator of strings, the name of each field in the schema
    """
    
    # we define a function _walk that produces a string generator from
    # a dictionnary "schema_dct", and a string "prefix"
    def _walk(schema_dct: Dict['str', Union['str', list, dict]],
              prefix: str = "") -> Generator[str, None, None]:
        assert isinstance(prefix, str), "prefix should be a string" # check if prefix is a string
        
        # this function returns "name" if there's no prefix and "prefix.name" if prefix exists
        fullName: Callable[str, str] = lambda name: ( 
            name if not prefix else f"{prefix}.{name}")
        
        # we get the next name one level lower from the dictionnary
        name = schema_dct.get('name', '')
        
        # if the type is struct then we search for the fields key
        # if fields is there we apply the function again and dig one level deeper in
        # the schema and set a prefix
        if schema_dct['type'] == 'struct':
            assert 'fields' in schema_dct, (
                "It's a StructType, we should have some fields")
            for field in schema_dct['fields']:
                yield from _walk(field, prefix=prefix)
        # if we have a dict type and we can't find fields then we
        # dig one level deeper and apply the _walk function again
        elif isinstance(schema_dct['type'], dict):
            assert 'fields' not in schema_dct, (
                "We're missing some keys here")
            yield from _walk(schema_dct['type'], prefix=fullName(name))
        # If we finally reached the end and found a name we yield the full name
        elif name:
            yield fullName(name)
    
    yield from _walk(schema.jsonValue())

# yield as opposed to return, returns a result but does not stop the function from running, it keeps
# running even after returning one result.

In [0]:
categorie_nb = df.select(F.explode('data.categories')).count()

In [0]:
display(categorie_nb)

191270

In [0]:
categorie_df = df.select(F.explode('data.categories')).distinct().show()

+--------------------+
|                 col|
+--------------------+
|   Remote Play on TV|
|         Steam Cloud|
|    In-App Purchases|
|Remote Play on Ta...|
|Remote Play Together|
|          Online PvP|
|Partial Controlle...|
|Full controller s...|
|        Multi-player|
|        Online Co-op|
| Steam Trading Cards|
|Valve Anti-Cheat ...|
|Remote Play on Phone|
| Shared/Split Screen|
|Shared/Split Scre...|
|       Single-player|
|               Co-op|
|Shared/Split Scre...|
|                 PvP|
|  Steam Achievements|
+--------------------+
only showing top 20 rows



In [0]:
genre_nb = df.select(F.col('data.genre')).distinct().count()
print(genre_nb)

1832


In [0]:
genre_df = df.select(F.col('data.genre')).distinct().show(10)

+--------------------+
|               genre|
+--------------------+
|Action, Adventure...|
|Action, Casual, I...|
|       Casual, Indie|
|Action, Indie, Si...|
|Action, Adventure...|
|Adventure, Indie,...|
|          Indie, RPG|
|Action, Adventure...|
|Action, Early Access|
|Action, RPG, Stra...|
+--------------------+
only showing top 10 rows



In [0]:
games_df=df.withColumn('id', F.col('id')) \
          .withColumn('app_id', F.col('data.appid')) \
          .withColumn('name', F.col('data.name')) \
          .withColumn('genre', F.col('data.genre')) \
          .withColumn('price', F.col('data.price')) \  
          .withColumn('publisher', F.col('data.publisher')) \
          .withColumn('type', F.col('data.type')) \
          .withColumn('required_age', F.col('data.required_age'))  \
          .withColumn('positive', F.col('data.positive'))  \
          .withColumn('negative', F.col('data.negative'))  \
          .withColumn('languages', F.col('data.languages'))  \
          .withColumn('discount', F.col('data.discount')) \
          .withColumn('release_date', F.to_timestamp(F.col("data.release_date"), format="y/M/d")) \
          .drop('data')
game_categories_df=df.withColumn('app_id', F.col('data.appid')) \
                     .withColumn('categories', F.explode('data.categories'))
games_df.select('name').orderBy(F.desc("positive")).show(15)
games_platform_df= df.withColumn('id', F.col('id')) \
                     .withColumn('linux', F.col('data.platforms.linux')) \
                     .withColumn('mac', F.col('data.platforms.mac')) \
                     .withColumn('windows', F.col('data.platforms.windows'))    
          


+--------------------+
|                name|
+--------------------+
|Counter-Strike: G...|
|              Dota 2|
|  Grand Theft Auto V|
| PUBG: BATTLEGROUNDS|
|            Terraria|
|Tom Clancy's Rain...|
|         Garry's Mod|
|     Team Fortress 2|
|                Rust|
|       Left 4 Dead 2|
|The Witcher 3: Wi...|
|            Among Us|
|Euro Truck Simula...|
|    Wallpaper Engine|
|            PAYDAY 2|
+--------------------+
only showing top 15 rows



In [0]:
games_platform_df.show(10)

+--------------------+-------+-----+-----+-------+
|                data|     id|linux|  mac|windows|
+--------------------+-------+-----+-----+-------+
|{10, [Multi-playe...|     10| true| true|   true|
|{1000000, [Single...|1000000|false|false|   true|
|{1000010, [Single...|1000010|false|false|   true|
|{1000030, [Multi-...|1000030|false| true|   true|
|{1000040, [Single...|1000040|false|false|   true|
|{1000080, [Multi-...|1000080|false| true|   true|
|{1000100, [Single...|1000100|false|false|   true|
|{1000110, [Multi-...|1000110|false|false|   true|
|{1000130, [Single...|1000130|false| true|   true|
|{1000280, [Single...|1000280|false|false|   true|
+--------------------+-------+-----+-----+-------+
only showing top 10 rows



In [0]:
nblinux=games_platform_df.filter((games_platform_df.linux)).count()
nbmac=games_platform_df.filter((games_platform_df.mac)).count()
nbwindows=games_platform_df.filter((games_platform_df.windows)).count()
print(f" linux games : {nblinux}, mac games : {nbmac}, windows games : {nbwindows}")


 linux games : 8458, mac games : 12770, windows games : 55676


In [0]:
games_nb = df.select(F.col('id')).distinct().count()
games_linux_nb=games_platform_df.filter(F.col('linux')== True ).count()
games_mac_nb=games_platform_df.filter(F.col('mac')== True ).count()
games_windows_nb=games_platform_df.filter(F.col('windows')== True ).count()
games_adult_nb =df.filter( \
    (F.col('data.required_age')!='0') \
     & (F.col('data.required_age')!='3') \
     & (F.col('data.required_age')!='5') \
     & (F.col('data.required_age')!='6') \
     & (F.col('data.required_age')!='7+') \
     & (F.col('data.required_age')!='8') \
     & (F.col('data.required_age')!='9') \
     & (F.col('data.required_age')!='10') \
     & (F.col('data.required_age')!='12') \
     & (F.col('data.required_age')!='13') \
     & (F.col('data.required_age')!='14')
     ).count()

categorie_age_nb=df.select('data.required_age').distinct().count()
print("nb de jeu  : ",games_nb)
print("nb jeu windows : ",games_windows_nb,"   mac : ", games_mac_nb, "  linux : ",games_linux_nb)
print("nb de jeu pour adulte  : ",games_adult_nb)
print("nombre de catégorie d'age : ",categorie_age_nb)
df.select('data.required_age').distinct().show()
#truc_df.show(30)

nb de jeu  :  55691
nb jeu windows :  55676    mac :  12770   linux :  8458
nb de jeu pour adulte  :  573
nombre de catégorie d'age :  21
+------------+
|required_age|
+------------+
|           7|
|          15|
|           3|
|           8|
|          16|
|          35|
|           0|
|         21+|
|           5|
|          18|
|          17|
|           6|
|         180|
|           9|
|          7+|
|          20|
|          10|
|          12|
|          13|
|          14|
+------------+
only showing top 20 rows



In [0]:
result_required_age=df.groupBy(F.col('data.required_age')).count().orderBy(F.desc("data.required_age"))
display(result_required_age)


required_age count MA 15+ 1 9 1 8 3 7+ 1 7 2 6 4 5 1 35 1 3 3 21+ 1 20 1 180 4 18 223 17 38 16 38 15 264 14 10 13 26 12 32 10 7 0 55030

Databricks visualization. Run in Databricks to view.

In [0]:
display(categorie_age_nb)

21

In [0]:
df.select('data.publisher').distinct().count()

Out[30]: 29966

In [0]:
result_publisher=games_df.groupBy('publisher').count().orderBy(F.desc("count")).limit(100)
display(result_publisher)


publisher count Big Fish Games 422 8floor 202 SEGA 165 Strategy First 151 Square Enix 141 Choice of Games 140 Sekai Project 132 HH-Games 132 132 Ubisoft 127 Laush Studio 126 THQ Nordic 125 Alawar Entertainment 107 Fulqrum Publishing 104 Plug In Digital 101 Ziggurat 100 Slitherine Ltd. 99 Sokpop Collective 99 Devolver Digital 98 KOEI TECMO GAMES CO., LTD. 90 Reforged Group 89 Electronic Arts 88 Komodo 87 PLAYISM 87 SA Industry 87 Microids 84 Piece Of Voxel 81 Hosted Games 79 Kagura Games 79 Boogygames Studios 78 Artifex Mundi 75 tinyBuild 72 Daedalic Entertainment 72 Blender Games 71 BANDAI NAMCO Entertainment 69 Paradox Interactive 69 Tero Lunkka 68 2K 67 My Way Games 66 ESDigital Games 64 Garage Games 62 MAGIX Software GmbH 62 Nacon 60 Forever Entertainment S. A. 60 RewindApp 59 Ripknot Systems 55 United Independent Entertainment 55 Bethesda Softworks 55 Back To Basics Gaming 54 Hede 54 MangaGamer 53 GrabTheGames 52 William at Oxford 52 Focus Entertainment 52 Activision 51 KEMCO 51 Ghost_RUS Games 50 Aldorlea Games 50 Individual Software 49 Sometimes You 49 Volens Nolens Games 47 Trinity Project 47 玫瑰工作室 47 Droid Riot 46 Iceberg Interactive 46 Atomic Fabrik, Cristian Manolachi 46 PsychoFlux Entertainment 46 Xbox Game Studios 46 Funbox Media Ltd 45 ImperiumGame 44 NIS America, Inc. 44 PQube 44 Dnovel 43 Kalypso Media Digital 43 HexWar Games 42 Enoops 42 8Floor 41 Pixel Games UK 41 505 Games 41 Atari 40 Big Black Bear 40 HandyGames 40 Winged Cloud 40 familyplay 40 Anamik Majumdar 40 Deep Silver 38 Team17 Digital Ltd 37 Rebellion 37 New Reality Games 37 HandMade Games 37 Disney 37 kovalevviktor 37 Headup 37 Bitlock Studio 37 Zoo Corporation 36 MumboJumbo 36 Qumaron 35 Piko Interactive LLC, Bleem! 35 GameHouse 35 Milestone S.r.l. 35

Databricks data profile. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:
result_languages=games_df.groupBy('languages').count().orderBy(F.desc("count"))
display(result_languages)

languages count English 29163 English, Russian 1881 English, Simplified Chinese 1200 English, Japanese 1015 English, Not supported, Simplified Chinese 683 English, German 605 English, French 510 English, French, Italian, German, Spanish - Spain 493 English, Portuguese - Brazil 463 English, Simplified Chinese, Traditional Chinese 326 Simplified Chinese 318 English, Spanish - Spain 300 English, French, German, Russian 268 English, French, Italian, German, Spanish - Spain, Arabic, Bulgarian, Portuguese - Brazil, Hungarian, Vietnamese, Greek, Danish, Spanish - Latin America, Traditional Chinese, Simplified Chinese, Korean, Dutch, Norwegian, Polish, Portuguese - Portugal, Romanian, Russian, Thai, Turkish, Ukrainian, Finnish, Czech, Swedish, Japanese 255 English, Japanese, Simplified Chinese, Traditional Chinese 208 English, Japanese, Simplified Chinese 208 English, Korean 206 English, French, Italian, German, Spanish - Spain, Arabic, Bulgarian, Czech, Danish, Dutch, Finnish, Greek, Hungarian, Japanese, Korean, Norwegian, Polish, Portuguese - Portugal, Portuguese - Brazil, Romanian, Russian, Simplified Chinese, Spanish - Latin America, Swedish, Thai, Traditional Chinese, Turkish, Ukrainian, Vietnamese 202 English, French, German 194 English, French, German, Italian, Spanish - Spain 178 English, Not supported, Japanese 171 English, Turkish 171 English, French, Italian, German, Spanish - Spain, Russian 162 English, French, German, Spanish - Spain 159 English, Polish 128 English, Simplified Chinese, Traditional Chinese, Japanese 126 English, Simplified Chinese, Japanese 125 English, Russian, Simplified Chinese 125 English, German, Russian 117 Simplified Chinese, English 107 English, Japanese, Traditional Chinese 100 English, Italian 95 English, Traditional Chinese 89 English, French, Italian, German, Spanish - Spain, Japanese 87 English, French, Italian, German, Spanish - Spain, Portuguese - Brazil 83 English, French, German, Spanish - Spain, Russian 81 English, French, Spanish - Spain 80 English, French, Italian, German, Spanish - Spain, Arabic, Bulgarian, Czech, Danish, Dutch, Finnish, Greek, Hungarian, Japanese, Korean, Norwegian, Polish, Portuguese - Portugal, Portuguese - Brazil, Romanian, Russian, Simplified Chinese, Swedish, Thai, Traditional Chinese, Turkish, Ukrainian 78 Japanese 71 English, Spanish - Latin America 69 English, Simplified Chinese, Russian 69 English, Russian, Ukrainian 69 English, Not supported, Simplified Chinese, Traditional Chinese 60 English, German, French, Italian, Spanish - Spain 59 English, Not supported, Traditional Chinese 58 English, Russian, German 53 English, French, Italian, German, Spanish - Spain, Japanese, Korean, Portuguese - Brazil, Russian, Simplified Chinese, Traditional Chinese 52 English, Japanese, Simplified Chinese, Traditional Chinese, Korean 51 English, French, Italian, German, Spanish - Spain, Danish, Ukrainian, Russian, Bulgarian, Hungarian, Turkish, Greek, Norwegian, Czech, Japanese, Polish, Thai, Swedish, Simplified Chinese, Traditional Chinese, Romanian, Finnish, Dutch, Portuguese - Portugal, Portuguese - Brazil, Spanish - Latin America, Vietnamese, Arabic, Korean 50 English, Japanese, Korean 49 English, Spanish - Spain, Spanish - Latin America 48 English, French, Italian, German, Spanish - Spain, Dutch 47 English, French, Italian, German, Spanish - Spain, Portuguese - Brazil, Russian 46 English, Not supported, Russian 45 English, French, Italian, German, Spanish - Spain, Arabic, Bulgarian, Portuguese - Brazil, Hungarian, Greek, Danish, Traditional Chinese, Simplified Chinese, Korean, Dutch, Norwegian, Polish, Portuguese - Portugal, Romanian, Russian, Thai, Turkish, Ukrainian, Finnish, Czech, Swedish, Japanese 45 English, Not supported, Korean 44 English, Simplified Chinese, Traditional Chinese, Japanese, Korean 44 English, German, Simplified Chinese, Portuguese - Portugal, Russian 43 English, Spanish - Spain, Portuguese - Brazil 43 English, French, Italian, German, Spanish - Spa

In [0]:
display(games_df.groupBy('release_date').count())

release_date count 2021-08-27T00:00:00.000+0000 38 2019-06-18T00:00:00.000+0000 16 2020-03-31T00:00:00.000+0000 31 2021-07-20T00:00:00.000+0000 48 2021-07-08T00:00:00.000+0000 26 2020-07-13T00:00:00.000+0000 24 2022-04-07T00:00:00.000+0000 30 2022-01-03T00:00:00.000+0000 15 2013-10-31T00:00:00.000+0000 3 2016-03-11T00:00:00.000+0000 12 2014-08-04T00:00:00.000+0000 4 2006-12-21T00:00:00.000+0000 2 2015-07-14T00:00:00.000+0000 5 2009-10-15T00:00:00.000+0000 1 2010-04-19T00:00:00.000+0000 1 2016-03-13T00:00:00.000+0000 1 2010-11-02T00:00:00.000+0000 3 2016-12-24T00:00:00.000+0000 1 2010-10-22T00:00:00.000+0000 1 2007-07-24T00:00:00.000+0000 1 2011-05-25T00:00:00.000+0000 1 2019-03-21T00:00:00.000+0000 21 2019-10-30T00:00:00.000+0000 22 2020-04-11T00:00:00.000+0000 6 2019-10-10T00:00:00.000+0000 33 2020-05-13T00:00:00.000+0000 26 2021-12-13T00:00:00.000+0000 18 2020-04-12T00:00:00.000+0000 4 2022-01-02T00:00:00.000+0000 4 2012-12-17T00:00:00.000+0000 1 2018-12-13T00:00:00.000+0000 19 2013-07-08T00:00:00.000+0000 1 2016-03-10T00:00:00.000+0000 11 2015-01-08T00:00:00.000+0000 11 2007-12-13T00:00:00.000+0000 2 2018-09-09T00:00:00.000+0000 7 2012-01-16T00:00:00.000+0000 1 2019-09-11T00:00:00.000+0000 33 2019-12-02T00:00:00.000+0000 20 2012-01-19T00:00:00.000+0000 4 2019-11-02T00:00:00.000+0000 5 2020-09-05T00:00:00.000+0000 6 2021-07-06T00:00:00.000+0000 13 2022-05-18T00:00:00.000+0000 37 2022-05-01T00:00:00.000+0000 8 2017-01-31T00:00:00.000+0000 19 2016-11-18T00:00:00.000+0000 29 2009-11-13T00:00:00.000+0000 3 2014-08-26T00:00:00.000+0000 5 2014-01-20T00:00:00.000+0000 1 2006-10-13T00:00:00.000+0000 4 2018-09-20T00:00:00.000+0000 37 2018-07-13T00:00:00.000+0000 51 2018-08-16T00:00:00.000+0000 30 2018-05-15T00:00:00.000+0000 35 2016-11-30T00:00:00.000+0000 23 2010-04-08T00:00:00.000+0000 1 2016-08-21T00:00:00.000+0000 1 2018-03-21T00:00:00.000+0000 22 2018-01-31T00:00:00.000+0000 34 2018-12-24T00:00:00.000+0000 20 2017-08-20T00:00:00.000+0000 2 2019-05-03T00:00:00.000+0000 22 2020-06-11T00:00:00.000+0000 33 2022-08-18T00:00:00.000+0000 39 2019-07-16T00:00:00.000+0000 17 2022-02-25T00:00:00.000+0000 37 2011-10-18T00:00:00.000+0000 3 2014-09-05T00:00:00.000+0000 8 2015-03-30T00:00:00.000+0000 10 2018-02-13T00:00:00.000+0000 43 2018-07-27T00:00:00.000+0000 32 2015-09-28T00:00:00.000+0000 9 2010-04-28T00:00:00.000+0000 4 2017-03-25T00:00:00.000+0000 1 2018-11-21T00:00:00.000+0000 22 2018-03-25T00:00:00.000+0000 6 2019-04-25T00:00:00.000+0000 37 2020-08-24T00:00:00.000+0000 20 2020-06-19T00:00:00.000+0000 34 2019-05-12T00:00:00.000+0000 3 2021-11-16T00:00:00.000+0000 37 2011-08-26T00:00:00.000+0000 8 2021-05-07T00:00:00.000+0000 33 2012-12-18T00:00:00.000+0000 1 2022-05-04T00:00:00.000+0000 21 2022-04-30T00:00:00.000+0000 11 2008-09-19T00:00:00.000+0000 1 2022-10-19T00:00:00.000+0000 22 2021-12-28T00:00:00.000+0000 9 2022-05-07T00:00:00.000+0000 6 1999-04-01T00:00:00.000+0000 1 2012-10-10T00:00:00.000+0000 2 2013-02-12T00:00:00.000+0000 1 2013-10-11T00:00:00.000+0000 4 2014-07-08T00:00:00.000+0000 5 2009-05-15T00:00:00.000+0000 1 2017-06-08T00:00:00.000+0000 30 2017-08-02T00:00:00.000+0000 29 2010-01-19T00:00:00.000+0000 1 2010-07-09T00:00:00.000+0000 4 2018-05-11T00:00:00.000+0000 27 2017-03-12T00:00:00.000+0000 1 2007-02-27T00:00:00.000+0000 1 2020-10-09T00:00:00.000+0000 31 2019-03-10T00:00:00.000+0000 4 2021-03-16T00:00:00.000+0000 28 2020-08-19T00:00:00.000+0000 18 2019-12-01T00:00:00.000+0000 3 2022-06-18T00:00:00.000+0000 12 2020-10-12T00:00:00.000+0000 22 2022-10-10T00:00:00.000+0000 28 2020-04-18T00:00:00.000+0000 10 2022-03-25T00:00:00.000+0000 33 2021-09-07T00:00:00.000+0000 26 2008-05-12T00:00:00.000+0000 3 2012-04-23T00:00:00.000+0000 4 2009-09-15T00:00:00.000+0000 3 2012-08-24T00:00:00.000+0000 3 2013-03-29T00:00:00.000+0000 1 2013-04-29T00:00:00.000+0000 2 2014-03-14T00:00:00.000+0000 6 2015-03-27T00:00:00.000+0000 13 1997-06-30T00:00:00.000+0000 1 2016-05-31T00:00:00.000+0000 20 2014-09-08T00:00:00.000+0000 1 2010-03-03T00

Databricks visualization. Run in Databricks to view.

Your boss gave you a list of examples of questions that would be interesting:

### Analysis at the "macro" level

Q : _Which publisher has released the most games on Steam?_ 

A : Big Fish Games is the publisher which has released the most games on Steam


Q : _What are the best rated games?_

A: the top rated games on steam platform are :
- Counter-Strike: Global Offensive
- Dota 2
- Grand Theft Auto 
- PUBG: BATTLEGROUNDS
- Terraria
- Tom Clancy's Rain...
- Garry's Mod
- Team Fortress 2
- Rust
- Left 4 Dead 2
- The Witcher 3: Wi..
- Among Us
- Euro Truck Simula...
- Wallpaper Engine
- PAYDAY 2


Q : _Are there years with more releases?_ 

A : Peak years are 2021 and 2020. Just after there are 2019 and 2022 years with a good figure for release.


Q: _Were there more or fewer game releases during the Covid, for example?_

A : There are more game releases in the worst part of the Covid (2020-2021)


Q : _How are the prizes distributed?_ 

A : 


Q : _Are there many games with a discount?_

A :


Q : _What are the most represented languages?_

A : English


Q : _Are there many games prohibited for children under 16/18 ?_

A : No, only 573 are rated for more than 16 years old people.


In [0]:
games_df.select('release_date').show(15)

+-------------------+
|       release_date|
+-------------------+
|2000-11-01 00:00:00|
|2021-05-14 00:00:00|
|2020-10-16 00:00:00|
|2020-10-14 00:00:00|
|2019-03-30 00:00:00|
|2019-06-24 00:00:00|
|2019-01-24 00:00:00|
|2019-04-08 00:00:00|
|2019-01-06 00:00:00|
|2021-09-09 00:00:00|
|2019-12-17 00:00:00|
|2021-02-16 00:00:00|
|2019-01-03 00:00:00|
|2019-02-01 00:00:00|
|2019-11-22 00:00:00|
+-------------------+
only showing top 15 rows



### Genres analysis

What are the most represented genres?



In [0]:
result_genre=games_df.groupBy(F.col('genre')).count().orderBy(F.desc("count")).limit(50)
display(result_genre)

genre count Action, Indie 3460 Casual, Indie 3060 Action, Adventure, Indie 2783 Adventure, Indie 2316 Action, Casual, Indie 1914 Adventure, Casual, Indie 1811 Indie 1756 Action 1633 Casual 1433 Adventure 1021 Action, Adventure, Casual, Indie 1018 Casual, Indie, Strategy 1000 Adventure, Casual 928 Adventure, Indie, RPG 867 Action, Adventure, Indie, RPG 807 Casual, Indie, Simulation 801 Action, Adventure 784 Strategy 779 Indie, Strategy 647 Simulation 579 RPG 534 Action, Indie, Early Access 498 Indie, Simulation, Strategy 470 Indie, RPG 444 Indie, Simulation 434 Casual, Indie, Simulation, Strategy 407 Action, Indie, RPG 379 Adventure, Casual, Indie, RPG 360 Action, Indie, Strategy 356 Simulation, Strategy 323 Action, Adventure, Indie, Early Access 315 Adventure, Casual, Indie, Simulation 294 Adventure, Indie, Simulation 272 Indie, RPG, Strategy 268 Action, Casual 266 Casual, Simulation 261 Action, Casual, Indie, Strategy 259 Action, Adventure, Indie, RPG, Early Access 246 Casual, Strategy 245 Action, Adventure, Casual, Indie, RPG 233 Action, Adventure, Indie, Simulation 230 Action, Indie, Simulation 230 Action, Adventure, RPG 229 Action, Casual, Indie, Early Access 226 Adventure, Indie, RPG, Strategy 213 Adventure, RPG 200 Action, Free to Play, Indie 200 Action, Adventure, Casual, Indie, Simulation 198 Utilities 197 Action, Casual, Indie, Simulation 191

Databricks visualization. Run in Databricks to view.

In [0]:
from pyspark.sql.functions import split
# a faire absoleument
#s=set()
#(s.add(ele) for ele in games_df.select(split(games_df.genre, ',').alias('nomtype')).show())
#games_df.select(split(games_df.genre, ',')).show()
uniques=games_df.select(split(games_df.genre, ',').alias('nomtype')).select('*', F.explode('nomtype').alias('genre_exploded'))
genre_unique_set = {str(row.genre_exploded).strip() for row in uniques.collect()}
action=games_df.filter(games_df.genre.contains("Action")).count()
simulation=games_df.filter(games_df.genre.contains("Simulation")).count()
adventure=games_df.filter(games_df.genre.contains("Adventure")).count()
strategy=games_df.filter(games_df.genre.contains("Strategy")).count()
indie=games_df.filter(games_df.genre.contains("Indie")).count()
casual=games_df.filter(games_df.genre.contains("Casual")).count()
print(f"action {action}, simulation {simulation}, adventure {adventure}, strategy {strategy}, indie {indie}, casual {casual} ")


action 23759, simulation 10836, adventure 21431, strategy 10895, indie 39681, casual 22086 


In [0]:
genre_unique_set

Out[48]: {'',
 'Accounting',
 'Action',
 'Adventure',
 'Animation & Modeling',
 'Audio Production',
 'Casual',
 'Design & Illustration',
 'Early Access',
 'Education',
 'Free to Play',
 'Game Development',
 'Gore',
 'Indie',
 'Massively Multiplayer',
 'Movie',
 'Nudity',
 'Photo Editing',
 'RPG',
 'Racing',
 'Sexual Content',
 'Simulation',
 'Software Training',
 'Sports',
 'Strategy',
 'Utilities',
 'Video Production',
 'Violent',
 'Web Publishing'}

In [0]:
genre_dict={}
for genre in genre_unique_set:
    genre_dict[genre]=games_df.filter(games_df.genre.contains(genre)).count()                               
display(genre_dict)

55691
10836
2666
10895
21431
89
105
45
195
2155
317
247
682
159
322
54
9534
1
164
1460
406
23759
168
6145
16
39681
22086
3393
99
{'': 55691,
 'Simulation': 10836,
 'Sports': 2666,
 'Strategy': 10895,
 'Adventure': 21431,
 'Web Publishing': 89,
 'Photo Editing': 105,
 'Nudity': 45,
 'Audio Production': 195,
 'Racing': 2155,
 'Education': 317,
 'Video Production': 247,
 'Utilities': 682,
 'Game Development': 159,
 'Animation & Modeling': 322,
 'Sexual Content': 54,
 'RPG': 9534,
 'Movie': 1,
 'Software Training': 164,
 'Massively Multiplayer': 1460,
 'Design & Illustration': 406,
 'Action': 23759,
 'Violent': 168,
 'Early Access': 6145,
 'Accounting': 16,
 'Indie': 39681,
 'Casual': 22086,
 'Free to Play': 3393,
 'Gore': 99}

In [0]:
for genre in genre_unique_set:
    print(f" The genre {genre} has {genre_dict[genre]} games.")

 The genre  has 55691 games.
 The genre Simulation has 10836 games.
 The genre Sports has 2666 games.
 The genre Strategy has 10895 games.
 The genre Adventure has 21431 games.
 The genre Web Publishing has 89 games.
 The genre Photo Editing has 105 games.
 The genre Nudity has 45 games.
 The genre Audio Production has 195 games.
 The genre Racing has 2155 games.
 The genre Education has 317 games.
 The genre Video Production has 247 games.
 The genre Utilities has 682 games.
 The genre Game Development has 159 games.
 The genre Animation & Modeling has 322 games.
 The genre Sexual Content has 54 games.
 The genre RPG has 9534 games.
 The genre Movie has 1 games.
 The genre Software Training has 164 games.
 The genre Massively Multiplayer has 1460 games.
 The genre Design & Illustration has 406 games.
 The genre Action has 23759 games.
 The genre Violent has 168 games.
 The genre Early Access has 6145 games.
 The genre Accounting has 16 games.
 The genre Indie has 39681 games.
 The gen

Are there any genres that have a better positive/negative review ratio?





In [0]:
genre_ratio={}
for genre in genre_unique_set:
    positive=games_df.filter(games_df.genre.contains(genre)).agg(F.sum("positive")).collect()[0][0]
    negative=games_df.filter(games_df.genre.contains(genre)).agg(F.sum("negative")).collect()[0][0]
    genre_ratio[genre]={"positive": positive,"negative": negative, "ratio":(float(positive)/flota(negative)) }
genre_ratio


Do some publishers have favorite genres?

What are the most lucrative genres?



### Platform analysis

Are most games available on Windows/Mac/Linux instead?

In [0]:
nblinux=games_platform_df.filter((games_platform_df.linux)).count()
nbmac=games_platform_df.filter((games_platform_df.mac)).count()
nbwindows=games_platform_df.filter((games_platform_df.windows)).count()
print(f" linux games : {nblinux}, mac games : {nbmac}, windows games : {nbwindows}")

 linux games : 8458, mac games : 12770, windows games : 55676


Do certain genres tend to be preferentially available on certain platforms?



You're free to follow these guidelines, or to choose a different angle of analysis, as long as your analysis reveals relevant and useful information. 🤓